In [26]:
!python3.7 -m pip install h5py tensorflow scipy==1.1.0 matplotlib

  Using cached https://files.pythonhosted.org/packages/9d/74/9eae2bedd8201ab464308f42c601a12d79727a1c87f0c867fdefb212c6cf/h5py-3.1.0-cp37-cp37m-manylinux1_x86_64.whl
  Using cached https://files.pythonhosted.org/packages/f4/28/96efba1a516cdacc2e2d6d081f699c001d414cc8ca3250e6d59ae657eb2b/tensorflow-1.14.0-cp37-cp37m-manylinux1_x86_64.whl
    100% |████████████████████████████████| 31.2MB 61kB/s eta 0:00:011
  Using cached https://files.pythonhosted.org/packages/30/f2/10c822cb0ca5ebec58bd1892187bc3e3db64a867ac26531c6204663fc218/matplotlib-3.3.3-cp37-cp37m-manylinux1_x86_64.whl
  Using cached https://files.pythonhosted.org/packages/5e/f2/9e562074f835b9b1227ca156f787be4554ae6bbe293c064337c4153cc4c8/numpy-1.19.4-cp37-cp37m-manylinux1_x86_64.whl
  Using cached https://files.pythonhosted.org/packages/48/19/f2090f7dad41e225c7f2326e4cfe6fff49e57dedb5b53636c9551f86b069/cached_property-1.5.2-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/bc/58/0aa6fb779dc69cfc811df339

We just use their tensorflow model from the paper imported, and use different functions for actually evaluating the depth map prediction and getting something from it. https://github.com/mrharicot/monodepth. You'll need python 3.7 to run this, and will also need to get the NYU depth dataset into this directory, named as nyu_depth_data_labeled.mat. We'll do all of that in the below cell - comment it out once you have run once.

In [27]:
#!wget http://horatio.cs.nyu.edu/mit/silberman/nyu_depth_data_labeled.mat
#!sh ./utils/get_model.sh model_kitti models/model_kitti

In [1]:
import numpy as np
import h5py

f = h5py.File('nyu_depth_data_labeled.mat')
images = f['images']
labels = f['labels']
depths = f['rawDepths']

In [2]:
# We want to normalize before getting the RMSE so that we won't have wildly different
# estimates for depth between this and Multi-Scale paper by David Eigen.
def normalize_np_array(npa):
    npa = npa.astype('int32')
    normalized = (255*(npa - np.min(npa))/np.ptp(npa)).astype(int)
    return normalized

In [3]:
from monodepth_model import *
from monodepth_dataloader import *
params = monodepth_parameters(
        encoder='vgg',
        height=256,
        width=512,
        batch_size=2,
        num_threads=1,
        num_epochs=1,
        do_stereo=False,
        wrap_mode="border",
        use_deconv=False,
        alpha_image_loss=0,
        disp_gradient_loss_weight=0,
        lr_loss_weight=0,
        full_summary=False)

/home/tphan/.local/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/tphan/.local/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/tphan/.local/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/home/tphan/.local/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:519: Futu

In [4]:
import scipy
import scipy.misc
import tensorflow as tf
import tensorflow.contrib.slim as slim
import matplotlib.pyplot as plt
import numpy as np

tf.reset_default_graph()

# We have prediction, which is 20 predictions of n x m images.
# targets is the same dimensions.
# To get the root mean squared error, we have to find 
def mean_squared_error(predictions, targets):
    return ((predictions - targets) ** 2).mean()

def post_process_disparity(disp):
    _, h, w = disp.shape
    l_disp = disp[0,:,:]
    r_disp = np.fliplr(disp[1,:,:])
    m_disp = 0.5 * (l_disp + r_disp)
    l, _ = np.meshgrid(np.linspace(0, 1, w), np.linspace(0, 1, h))
    l_mask = 1.0 - np.clip(20 * (l - 0.05), 0, 1)
    r_mask = np.fliplr(l_mask)
    return r_mask * l_disp + l_mask * r_disp + (1.0 - l_mask - r_mask) * m_disp

# We can use this to test an image against its depth labels, and return its mean squared error.
def test_simple_with_image_and_labels(params, input_image, labels, checkpoint_path, input_height, input_width, output_name='yikes'):
    """Test function."""

    left  = tf.placeholder(tf.float32, [2, input_height, input_width, 3])
    model = MonodepthModel(params, "test", left, None)
    input_image = np.transpose(input_image, (1, 2, 0))
    original_height, original_width, num_channels = input_image.shape
    input_image = scipy.misc.imresize(input_image, [input_height, input_width], interp='lanczos')
    #plt.imsave("raw{}.png".format(output_name), input_image)
    input_image = input_image.astype(np.float32) / 255
    input_images = np.stack((input_image, np.fliplr(input_image)), 0)

    # SESSION
    config = tf.ConfigProto(allow_soft_placement=True)
    sess = tf.Session(config=config)

    # SAVER
    train_saver = tf.train.Saver()

    # INIT
    sess.run(tf.global_variables_initializer())
    sess.run(tf.local_variables_initializer())
    coordinator = tf.train.Coordinator()
    threads = tf.train.start_queue_runners(sess=sess, coord=coordinator)

    # RESTORE
    restore_path = checkpoint_path.split(".")[0]
    train_saver.restore(sess, restore_path)

    disp = sess.run(model.disp_left_est[0], feed_dict={left: input_images})
    disp_pp = post_process_disparity(disp.squeeze()).astype(np.float32)

    disp_to_img = scipy.misc.imresize(disp_pp.squeeze(), [original_height, original_width])
    resized = np.rot90(scipy.misc.imresize(disp_to_img, [640, 480]), 0)
    #plt.imsave("{}.png".format(output_name), resized, cmap='gray')
    # We have it, but resized to original size - let's check what it is
    normalized_prediction = normalize_np_array(disp_to_img)
    return mean_squared_error(normalized_prediction, labels)

In [7]:
import pathlib

# This goes through the first 200 images and makes a list of mean-squared errors, mses - it becomes
# trivial to calculate root mean squared error in the next cells.
mses = []
iterations = 0
max_iterations = 200
for im, lb in zip(images, depths):
    tf.reset_default_graph()
    d = normalize_np_array(lb)
    mses.append(test_simple_with_image_and_labels(params, im, d, f'{pathlib.Path().absolute()}/models/model_kitti/model_kitti', 256, 512, iterations))
    iterations += 1
    print(f'Iteration number {iterations}')
    if iterations >= max_iterations:
        break
mses

(256, 512, 3)


/home/tphan/.local/lib/python3.7/site-packages/ipykernel_launcher.py:34: DeprecationWarning:     `imresize` is deprecated!
    `imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
    Use ``skimage.transform.resize`` instead.


INFO:tensorflow:Restoring parameters from /home/tphan/AdvancedMLProjects/AdvancedMLFinal/monodepth/models/model_kitti/model_kitti
Iteration number 1


/home/tphan/.local/lib/python3.7/site-packages/ipykernel_launcher.py:61: DeprecationWarning:     `imresize` is deprecated!
    `imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
    Use ``skimage.transform.resize`` instead.
/home/tphan/.local/lib/python3.7/site-packages/ipykernel_launcher.py:62: DeprecationWarning:     `imresize` is deprecated!
    `imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
    Use ``skimage.transform.resize`` instead.


(256, 512, 3)
INFO:tensorflow:Restoring parameters from /home/tphan/AdvancedMLProjects/AdvancedMLFinal/monodepth/models/model_kitti/model_kitti
Iteration number 2


...

(256, 512, 3)
INFO:tensorflow:Restoring parameters from /home/tphan/AdvancedMLProjects/AdvancedMLFinal/monodepth/models/model_kitti/model_kitti
Iteration number 197


(256, 512, 3)
INFO:tensorflow:Restoring parameters from /home/tphan/AdvancedMLProjects/AdvancedMLFinal/monodepth/models/model_kitti/model_kitti
Iteration number 198


(256, 512, 3)
INFO:tensorflow:Restoring parameters from /home/tphan/AdvancedMLProjects/AdvancedMLFinal/monodepth/models/model_kitti/model_kitti
Iteration number 199


(256, 512, 3)
INFO:tensorflow:Restoring parameters from /home/tphan/AdvancedMLProjects/AdvancedMLFinal/monodepth/models/model_kitti/model_kitti
Iteration number 200


[9426.140953776041,
 15757.805921223959,
 12116.04240234375,
 20233.410924479165,
 16196.13146484375,
 12426.754319661459,
 12297.156025390625,
 10289.688444010417,
 14546.088287760416,
 13265.034446614583,
 9442.93609375,
 7325.284156901042,
 5783.365511067708,
 6136.965970052083,
 6080.787649739584,
 6033.184847005208,
 9264.574153645834,
 4593.029781901042,
 8206.231959635417,
 4041.886435546875,
 8750.668857421875,
 9433.956829427083,
 5462.5787890625,
 7518.856555989583,
 8998.585,
 5241.316848958333,
 4177.124781901041,
 14935.60611328125,
 18793.72586263021,
 18107.253365885415,
 19802.66251953125,
 26212.16229817708,
 18715.54394205729,
 19036.308916015623,
 24509.23275390625,
 24025.2602734375,
 23079.677001953125,
 22986.524384765624,
 23009.538284505208,
 25887.10337239583,
 29852.418626302082,
 15250.369065755209,
 22582.79294596354,
 16003.310992838542,
 7946.268984375,
 9500.730947265625,
 16934.001497395835,
 20029.76144205729,
 6883.393707682291,
 6575.804026692708,
 75

In [8]:
mean_of_mses = sum(mses) / len(mses)
import math
print(math.sqrt(mean_of_mses))

121.3137774981572
